In [17]:
import requests
from bs4 import BeautifulSoup
from time import sleep
import pandas as pd
import numpy as np
import random
import json
import urllib
import re
from selenium import webdriver

import html

In [138]:
def get_html(url):
    r = requests.get(url)
    return r.text

def get_book_info(url):
    html = get_html(url)
    id_paper = int(url.split('/')[5])
    soup = BeautifulSoup(html, 'html.parser')
    image_src = soup.find_all('div', class_='product__image')[0].findAll("img")[0]
    image = image_src.attrs['src']
    
    name = soup.find_all('h1', itemprop='name')[0].text
    author = soup.find_all('a', class_='link product__author')[0].text.strip()
    
    rating = soup.find_all('div', class_='rating')[0].find('span').text
    stars = rating.split(' ')[0]
    voters = rating.split(' (')[1].split(')')[0]
    
    # add try
    try:
        price = soup.find_all('div', class_='price')[0].text.strip().split(' ')[0]
    except:
        price = 'Не указана'
    
    data = soup.find_all('div', class_='product-prop')
    data_table = [[data[i].find('div', class_='product-prop__title').text.strip(),
                   data[i].find('div', class_='product-prop__value').text.strip()]
                  for i, _ in enumerate(data)]
    all_data = {'ID': id_paper, 'image': image, 'name': name,
                'author': author, 'stars': stars, 'voters': voters,
                'price': price, 'table': data_table}
    return all_data

def book_dataframe(data):
    df = pd.DataFrame(index=np.arange(1), columns=['ID карточки', 'ID товара:', 'ISBN', 'Автор', 'Возраст', 
                   'Год издания', 'Голоса', 'Издательство', 'Кол-во страниц',
                   'Название', 'Переводчик', 'Редактор', 'Рейтинг', 'Серия',
                   'Тип обложки', 'Тираж', 'Формат', 'Художник', 'Цена', 'Обложка'])
    df['ID карточки'] = data['ID']
    df['Обложка'] = data['image']
    df['Название'] = data['name']
    df['Автор'] = data['author']
    df['Рейтинг'] = data['stars']
    df['Голоса'] = data['voters']
    df['Цена'] = data['price']

    for item in data['table']:
        df[item[0]] = item[1]
    return df

def get_ids(url):
    ids = []
    with webdriver.Chrome('/home/Albert/Загрузки/chromedriver_linux64/chromedriver') as driver:
        driver.get(url)
        i = 2    
        length = driver.find_elements_by_class_name("count-result")
        count = length[0].find_elements_by_class_name('count-result__value')[0].text

        items = driver.find_elements_by_class_name("product-card")
        while (len(items) != int(count)):
            driver.execute_script("window.scrollTo(0, {0}000);".format(i))
            sleep(4)
            i += 2
            driver.execute_script("window.scrollTo(0, {0}000);".format(i))
            sleep(4)
            try:
                play = driver.find_element_by_class_name('js__show-more-cards')
                play.click()
            except:
                pass
            sleep(5)
            items = driver.find_elements_by_class_name("product-card")
            i *= 4
            driver.execute_script("window.scrollTo(0, {0}000);".format(i))
            sleep(4)
            i += 2
            driver.execute_script("window.scrollTo(0, {0}000);".format(i))

        items = driver.find_elements_by_class_name("product-card")
        for item in items:
             ids.append(item.get_attribute('data-product'))
                
    return ids

def all_book_urls(ids):
    books_urls = ['https://www.chitai-gorod.ru/catalog/book/' + x 
                  + '/?watch_fromlist=search_result' for x in ids]
    return books_urls

def get_all_books(url):
    ids = get_ids(url)
    books_urls = all_book_urls(ids)
    
    data = pd.DataFrame()
    df = pd.DataFrame()
    i = 1
    for url in books_urls:
        print(i, end='  ')
        i += 1
        df = book_dataframe(get_book_info(url))
        frame = [data, df]
        data = pd.concat(frame)
    return data

In [41]:
m_fry = urllib.parse.quote("Фрай М.", encoding="cp1251")
m_fry

'%D4%F0%E0%E9%20%CC.'

In [42]:
('https://www.chitai-gorod.ru/search/result.php?q={0}&type=author').format(m_fry)

'https://www.chitai-gorod.ru/search/result.php?q=%D4%F0%E0%E9%20%CC.&type=author'

In [7]:
# url_m_fray = ('https://www.chitai-gorod.ru/search/result.php?q={0}&type=author').format(m_fry)
url = 'https://www.chitai-gorod.ru/catalog/book/246914/?watch_fromlist=search_result'
id_paper = url.split('/')
html = get_html(url)
soup = BeautifulSoup(html, 'html.parser')

In [11]:
image_src = soup.find_all('div', class_='product__image')[0].findAll("img")[0]
image = image_src.attrs['src']
image
# name = soup.find_all('h1', itemprop='name')[0].text
# name

'https://img-gorod.ru/upload/iblock/6c2/6c220c8a61d7d3081889da1f9721a2a6.jpg'

In [124]:
import re
data = soup.find_all('div', class_='product-prop')
# ser = [i.text for i in seria]
# list(map(lambda x: re.sub("\s+", ' ', x.strip()), ser))
# tb = [i.text.strip() for i in data]

# table = list(map(lambda x: re.sub("\s+", ' ', x.strip()), tb))
data_table = [[data[i].find('div', class_='product-prop__title').text.strip(),
               data[i].find('div', class_='product-prop__value').text.strip()]
              for i, _ in enumerate(data)]

In [125]:
data_table

[['Серия', 'Лабиринты Ехо'],
 ['Издательство', 'Амфора, ООО'],
 ['Год издания', '2009'],
 ['Кол-во страниц', '383'],
 ['ISBN', '9785942783884'],
 ['Тираж', '5000'],
 ['Формат', '20.6 x 13.7 x 2.5'],
 ['Тип обложки', 'Твердая бумажная'],
 ['Возраст', '12+'],
 ['ID товара:', '1807966']]

In [14]:
data = get_book_info(url)

In [15]:
data

{'ID': 246914,
 'image': 'https://img-gorod.ru/upload/iblock/6c2/6c220c8a61d7d3081889da1f9721a2a6.jpg',
 'name': 'Наваждения',
 'author': 'Фрай М.',
 'stars': '0',
 'voters': '0',
 'price': '427',
 'table': [['Серия', 'Лабиринты Ехо'],
  ['Издательство', 'Амфора, ООО'],
  ['Год издания', '2009'],
  ['Кол-во страниц', '383'],
  ['ISBN', '9785942783884'],
  ['Тираж', '5000'],
  ['Формат', '20.6 x 13.7 x 2.5'],
  ['Тип обложки', 'Твердая бумажная'],
  ['Возраст', '12+'],
  ['ID товара:', '1807966']]}

In [30]:
df = pd.DataFrame(index=np.arange(1), columns=['ID карточки', 'ID товара:', 'ISBN', 'Автор', 'Возраст', 
                   'Год издания', 'Голоса', 'Издательство', 'Кол-во страниц',
                   'Название', 'Переводчик', 'Редактор', 'Рейтинг', 'Серия',
                   'Тип обложки', 'Тираж', 'Формат', 'Художник', 'Цена', 'Обложка'])
df['ID карточки'] = data['ID']
df['Обложка'] = data['image']
df['Название'] = data['name']
df['Автор'] = data['author']
df['Рейтинг'] = data['stars']
df['Голоса'] = data['voters']
df['Цена'] = data['price']

for item in data['table']:
    df[item[0]] = item[1]

df

ID карточки ID товара:           ISBN    Автор Возраст Год издания Голоса  \
0       246914    1807966  9785942783884  Фрай М.     12+        2009      0   

  Издательство Кол-во страниц    Название Переводчик Редактор Рейтинг  \
0  Амфора, ООО            383  Наваждения        NaN      NaN       0   

           Серия       Тип обложки Тираж             Формат Художник Цена  \
0  Лабиринты Ехо  Твердая бумажная  5000  20.6 x 13.7 x 2.5      NaN  427   

                                             Обложка  
0  https://img-gorod.ru/upload/iblock/6c2/6c220c8...

In [28]:
df['ID карточки'] = data['ID']
df

ID карточки ID товара: ISBN Автор Возраст Год издания Голоса Издательство  \
0       246914        NaN  NaN   NaN     NaN         NaN    NaN          NaN   

  Кол-во страниц Название Переводчик Редактор Рейтинг Серия Тип обложки Тираж  \
0            NaN      NaN        NaN      NaN     NaN   NaN         NaN   NaN   

  Формат Художник Цена Обложка  
0    NaN      NaN  NaN     NaN

In [32]:
url1 = 'https://www.chitai-gorod.ru/catalog/book/888578/?watch_fromlist=search_result'
url2 = 'https://www.chitai-gorod.ru/catalog/book/765102/?watch_fromlist=search_result'

data1 = get_book_info(url1)
data2 = get_book_info(url2)

In [38]:
df1 = book_dataframe(data1)
df2 = book_dataframe(data2)
df0 = pd.DataFrame()
frame = [df0, df1]#, df2]
df0 = pd.concat(frame)
df0

ID карточки ID товара:           ISBN    Автор Возраст Год издания Голоса  \
0       888578    2509026  9785170952670  Фрай М.     18+        2016      2   

  Издательство Кол-во страниц       Название Переводчик Редактор Рейтинг  \
0          АСТ            480  Карты на стол        NaN      NaN       4   

             Серия       Тип обложки  Тираж           Формат Художник Цена  \
0  Миры Макса Фрая  Твердая бумажная  15000  20.5 x 13 x 2.5      NaN  332   

                                             Обложка  
0  https://img-gorod.ru/upload/iblock/85d/85d08a7...

In [78]:
url = 'https://www.chitai-gorod.ru/search/result.php?q=%D4%F0%E0%E9%20%CC.&type=author'
soup =  BeautifulSoup(get_html(url), 'html.parser')
import time

'window.scrollTo(0, 1000);'

In [87]:
soup


<!DOCTYPE html>

<html dir="ltr" ng-app="search">
<head>
<link href="https://img-gorod.ru" rel="dns-prefetch"/>
<meta content="IE=edge" http-equiv="X-UA-Compatible"/>
<meta content="text/html; charset=utf-8" http-equiv="Content-Type"/>
<meta content="65c799ed1259b388" name="yandex-verification"/>
<meta content="05725c0ecd32a193" name="yandex-verification"/>
<meta content="9733050c10fc15ab" name="yandex-verification"/>
<meta content="hA8vdpybpjnGvyu1SpXRYZo9iv068BCHmT7Y6QVfcSc" name="google-site-verification"/>
<meta content="noyaca" name="robots"/>
<meta content=" " name="keywords"/>
<title>Результаты поиска	</title>
<link href="/bitrix/components/kav/subscribe/templates/.default/style.css?1497429415104" rel="stylesheet" type="text/css"/>
<link href="/bitrix/components/kav/chitai.socialauth/templates/.default/style.css?14974294151301" rel="stylesheet" type="text/css"/>
<!-- BEGIN JIVOSITE CODE -->
<script type="text/javascript">
(function(){ var widget_id = '108059';
var s = document.

In [90]:
length = soup.find_all('div', class_='count-result')
length

[<div class="count-result">Найдено <span class="count-result__value">{{indexVM.results.hits.total}}</span> товара
 				</div>]

In [100]:

with webdriver.Chrome('/home/Albert/Загрузки/chromedriver_linux64/chromedriver') as driver:
    driver.get(url)
    length = driver.find_elements_by_class_name("count-result")
    print(length[0])
    count = length[0].find_elements_by_class_name('count-result__value')[0].text
count

<selenium.webdriver.remote.webelement.WebElement (session="78c793e7d91eb91d085af8f12a0a29da", element="0.8241965052910374-1")>


'153'

In [107]:
ids = []
with webdriver.Chrome('/home/Albert/Загрузки/chromedriver_linux64/chromedriver') as driver:
    driver.get(url)
    i = 2    
    length = driver.find_elements_by_class_name("count-result")
    count = length[0].find_elements_by_class_name('count-result__value')[0].text
    
    items = driver.find_elements_by_class_name("product-card")
    while (len(items) != int(count)):
        driver.execute_script("window.scrollTo(0, {0}000);".format(i))
        sleep(4)
        i += 2
        driver.execute_script("window.scrollTo(0, {0}000);".format(i))
        sleep(4)
        try:
            play = driver.find_element_by_class_name('js__show-more-cards')
            play.click()
        except:
            pass
        sleep(5)
        items = driver.find_elements_by_class_name("product-card")
        i *= 4
        driver.execute_script("window.scrollTo(0, {0}000);".format(i))
        sleep(4)
        i += 2
        driver.execute_script("window.scrollTo(0, {0}000);".format(i))
    
    items = driver.find_elements_by_class_name("product-card")
    for item in items:
         ids.append(item.get_attribute('data-product'))

In [108]:
len(ids)

153

In [109]:
ids

['244296',
 '245728',
 '246246',
 '246247',
 '246533',
 '246749',
 '246913',
 '246914',
 '247198',
 '247199',
 '247200',
 '247406',
 '248903',
 '253620',
 '256186',
 '259037',
 '259751',
 '259790',
 '266507',
 '266508',
 '268263',
 '270861',
 '271107',
 '271108',
 '272859',
 '274724',
 '274979',
 '280462',
 '291153',
 '292170',
 '293276',
 '296766',
 '300551',
 '300799',
 '301879',
 '302904',
 '305522',
 '305523',
 '309851',
 '310895',
 '310896',
 '312706',
 '323381',
 '324455',
 '350170',
 '353710',
 '354139',
 '354742',
 '358088',
 '358727',
 '361307',
 '361874',
 '364589',
 '367135',
 '376401',
 '377037',
 '379158',
 '389640',
 '389641',
 '392051',
 '392052',
 '400412',
 '411548',
 '411549',
 '411550',
 '411551',
 '411552',
 '411553',
 '411625',
 '411626',
 '411627',
 '411628',
 '411629',
 '411682',
 '411683',
 '411692',
 '411693',
 '411732',
 '411733',
 '411750',
 '442981',
 '442982',
 '471783',
 '710328',
 '723716',
 '765102',
 '779618',
 '784979',
 '789215',
 '790009',
 '793750',

In [111]:
books_urls = ['https://www.chitai-gorod.ru/catalog/book/' + x 
                  + '/?watch_fromlist=search_result' for x in ids]
books_urls

['https://www.chitai-gorod.ru/catalog/book/244296/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/245728/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/246246/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/246247/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/246533/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/246749/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/246913/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/246914/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/247198/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/247199/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/247200/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/247406/?watch_fromlist=search_result',
 'https://www.ch

In [115]:
data = pd.DataFrame()
url = 'https://www.chitai-gorod.ru/search/result.php?q=%D4%F0%E0%E9%20%CC.&type=author'
data = get_all_books(url)

IndexError: list index out of range

In [116]:
ids = get_ids(url)
books_urls = all_book_urls(ids)
books_urls

['https://www.chitai-gorod.ru/catalog/book/244296/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/245728/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/246246/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/246247/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/246533/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/246749/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/246913/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/246914/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/247198/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/247199/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/247200/?watch_fromlist=search_result',
 'https://www.chitai-gorod.ru/catalog/book/247406/?watch_fromlist=search_result',
 'https://www.ch

In [128]:
# html = get_html(url)
id_paper = int(url.split('/')[5])
soup = BeautifulSoup(html, 'html.parser')
image_src = soup.find_all('div', class_='product__image')[0].findAll("img")[0]
image = image_src.attrs['src']
    
name = soup.find_all('h1', itemprop='name')[0].text
author = soup.find_all('a', class_='link product__author')[0].text.strip()
  
rating = soup.find_all('div', class_='rating')[0].find('span').text
stars = rating.split(' ')[0]
voters = rating.split(' (')[1].split(')')[0]
    
price = soup.find_all('div', class_='price')[0].text.strip().split(' ')[0]
    
# data = soup.find_all('div', class_='product-prop')
# data_table = [[data[i].find('div', class_='product-prop__title').text.strip(),
#                data[i].find('div', class_='product-prop__value').text.strip()]
#                for i, _ in enumerate(data)]
# all_data = {'ID': id_paper, 'image': image, 'name': name,
#             'author': author, 'stars': stars, 'voters': voters,
#             'price': price, 'table': data_table}

IndexError: list index out of range

In [129]:
soup.find_all('div', class_='price')

[]

In [121]:
html = get_html('https://www.chitai-gorod.ru/catalog/book/244296/?watch_fromlist=search_result')

In [131]:
data = pd.DataFrame()
df = pd.DataFrame()

for url in books_urls:
        df = book_dataframe(get_book_info(url))
        frame = [data, df]
        data = pd.concat(frame)
        print(data)

   ID карточки ID товара:           ISBN    Автор Возраст Год издания Голоса  \
0       244296    1400705  9785367009781  Фрай М.     NaN        2009      0   

  Издательство Кол-во страниц                Название Переводчик Редактор  \
0  Амфора, ООО            478  Книга для таких, как я        NaN      NaN   

  Рейтинг Серия       Тип обложки Тираж           Формат Художник        Цена  \
0       0  ФРАМ  Твердая бумажная  4000  20.5 x 13.2 x 3      NaN  Не указана   

                                             Обложка  
0  https://img-gorod.ru/upload/iblock/73b/73b0845...  
   ID карточки ID товара:           ISBN    Автор Возраст Год издания Голоса  \
0       244296    1400705  9785367009781  Фрай М.     NaN        2009      0   
0       245728    1665067  9785942783372  Фрай М.     NaN        2010      0   

  Издательство Кол-во страниц                Название Переводчик Редактор  \
0  Амфора, ООО            478  Книга для таких, как я        NaN      NaN   
0  Амфора, ООО  

   ID карточки ID товара:           ISBN    Автор Возраст Год издания Голоса  \
0       244296    1400705  9785367009781  Фрай М.     NaN        2009      0   
0       245728    1665067  9785942783372  Фрай М.     NaN        2010      0   
0       246246    1801350     5942783535  Фрай М.     NaN        2003      0   
0       246247    1801351  9785367016239  Фрай М.     NaN        2009      0   
0       246533    1804075  9785942783600  Фрай М.     12+        2013      1   
0       246749    1806167  9785942783877  Фрай М.     12+        2013      0   
0       246913    1807965  9785367003390  Фрай М.     NaN        2003      0   

  Издательство Кол-во страниц                Название Переводчик  \
0  Амфора, ООО            478  Книга для таких, как я        NaN   
0  Амфора, ООО            606      Волонтеры вечности        NaN   
0  Амфора, ООО            350  Простые волшебные вещи        NaN   
0  Амфора, ООО            367          Темная сторона        NaN   
0  Амфора, ООО     

   ID карточки ID товара:           ISBN    Автор Возраст Год издания Голоса  \
0       244296    1400705  9785367009781  Фрай М.     NaN        2009      0   
0       245728    1665067  9785942783372  Фрай М.     NaN        2010      0   
0       246246    1801350     5942783535  Фрай М.     NaN        2003      0   
0       246247    1801351  9785367016239  Фрай М.     NaN        2009      0   
0       246533    1804075  9785942783600  Фрай М.     12+        2013      1   
0       246749    1806167  9785942783877  Фрай М.     12+        2013      0   
0       246913    1807965  9785367003390  Фрай М.     NaN        2003      0   
0       246914    1807966  9785942783884  Фрай М.     12+        2009      0   
0       247198    1810879  9785367004069  Фрай М.     NaN        2003      0   
0       247199    1810880  9785942782429  Фрай М.     NaN        2006      0   

  Издательство Кол-во страниц                        Название Переводчик  \
0  Амфора, ООО            478          Книг

   ID карточки ID товара:           ISBN    Автор Возраст Год издания Голоса  \
0       244296    1400705  9785367009781  Фрай М.     NaN        2009      0   
0       245728    1665067  9785942783372  Фрай М.     NaN        2010      0   
0       246246    1801350     5942783535  Фрай М.     NaN        2003      0   
0       246247    1801351  9785367016239  Фрай М.     NaN        2009      0   
0       246533    1804075  9785942783600  Фрай М.     12+        2013      1   
0       246749    1806167  9785942783877  Фрай М.     12+        2013      0   
0       246913    1807965  9785367003390  Фрай М.     NaN        2003      0   
0       246914    1807966  9785942783884  Фрай М.     12+        2009      0   
0       247198    1810879  9785367004069  Фрай М.     NaN        2003      0   
0       247199    1810880  9785942782429  Фрай М.     NaN        2006      0   
0       247200    1810881  9785367003406  Фрай М.     NaN        2009      0   
0       247406    1813266  9785942784362

   ID карточки ID товара:           ISBN    Автор Возраст Год издания Голоса  \
0       244296    1400705  9785367009781  Фрай М.     NaN        2009      0   
0       245728    1665067  9785942783372  Фрай М.     NaN        2010      0   
0       246246    1801350     5942783535  Фрай М.     NaN        2003      0   
0       246247    1801351  9785367016239  Фрай М.     NaN        2009      0   
0       246533    1804075  9785942783600  Фрай М.     12+        2013      1   
0       246749    1806167  9785942783877  Фрай М.     12+        2013      0   
0       246913    1807965  9785367003390  Фрай М.     NaN        2003      0   
0       246914    1807966  9785942783884  Фрай М.     12+        2009      0   
0       247198    1810879  9785367004069  Фрай М.     NaN        2003      0   
0       247199    1810880  9785942782429  Фрай М.     NaN        2006      0   
0       247200    1810881  9785367003406  Фрай М.     NaN        2009      0   
0       247406    1813266  9785942784362

...

    ID карточки ID товара:           ISBN    Автор Возраст Год издания Голоса  \
0        244296    1400705  9785367009781  Фрай М.     NaN        2009      0   
0        245728    1665067  9785942783372  Фрай М.     NaN        2010      0   
0        246246    1801350     5942783535  Фрай М.     NaN        2003      0   
0        246247    1801351  9785367016239  Фрай М.     NaN        2009      0   
0        246533    1804075  9785942783600  Фрай М.     12+        2013      1   
0        246749    1806167  9785942783877  Фрай М.     12+        2013      0   
0        246913    1807965  9785367003390  Фрай М.     NaN        2003      0   
0        246914    1807966  9785942783884  Фрай М.     12+        2009      0   
0        247198    1810879  9785367004069  Фрай М.     NaN        2003      0   
0        247199    1810880  9785942782429  Фрай М.     NaN        2006      0   
0        247200    1810881  9785367003406  Фрай М.     NaN        2009      0   
0        247406    1813266  

    ID карточки ID товара:           ISBN    Автор Возраст Год издания Голоса  \
0        244296    1400705  9785367009781  Фрай М.     NaN        2009      0   
0        245728    1665067  9785942783372  Фрай М.     NaN        2010      0   
0        246246    1801350     5942783535  Фрай М.     NaN        2003      0   
0        246247    1801351  9785367016239  Фрай М.     NaN        2009      0   
0        246533    1804075  9785942783600  Фрай М.     12+        2013      1   
0        246749    1806167  9785942783877  Фрай М.     12+        2013      0   
0        246913    1807965  9785367003390  Фрай М.     NaN        2003      0   
0        246914    1807966  9785942783884  Фрай М.     12+        2009      0   
0        247198    1810879  9785367004069  Фрай М.     NaN        2003      0   
0        247199    1810880  9785942782429  Фрай М.     NaN        2006      0   
0        247200    1810881  9785367003406  Фрай М.     NaN        2009      0   
0        247406    1813266  

    ID карточки ID товара:           ISBN    Автор Возраст Год издания Голоса  \
0        244296    1400705  9785367009781  Фрай М.     NaN        2009      0   
0        245728    1665067  9785942783372  Фрай М.     NaN        2010      0   
0        246246    1801350     5942783535  Фрай М.     NaN        2003      0   
0        246247    1801351  9785367016239  Фрай М.     NaN        2009      0   
0        246533    1804075  9785942783600  Фрай М.     12+        2013      1   
0        246749    1806167  9785942783877  Фрай М.     12+        2013      0   
0        246913    1807965  9785367003390  Фрай М.     NaN        2003      0   
0        246914    1807966  9785942783884  Фрай М.     12+        2009      0   
0        247198    1810879  9785367004069  Фрай М.     NaN        2003      0   
0        247199    1810880  9785942782429  Фрай М.     NaN        2006      0   
0        247200    1810881  9785367003406  Фрай М.     NaN        2009      0   
0        247406    1813266  

    ID карточки ID товара:           ISBN    Автор Возраст Год издания Голоса  \
0        244296    1400705  9785367009781  Фрай М.     NaN        2009      0   
0        245728    1665067  9785942783372  Фрай М.     NaN        2010      0   
0        246246    1801350     5942783535  Фрай М.     NaN        2003      0   
0        246247    1801351  9785367016239  Фрай М.     NaN        2009      0   
0        246533    1804075  9785942783600  Фрай М.     12+        2013      1   
0        246749    1806167  9785942783877  Фрай М.     12+        2013      0   
0        246913    1807965  9785367003390  Фрай М.     NaN        2003      0   
0        246914    1807966  9785942783884  Фрай М.     12+        2009      0   
0        247198    1810879  9785367004069  Фрай М.     NaN        2003      0   
0        247199    1810880  9785942782429  Фрай М.     NaN        2006      0   
0        247200    1810881  9785367003406  Фрай М.     NaN        2009      0   
0        247406    1813266  

    ID карточки ID товара:           ISBN    Автор Возраст Год издания Голоса  \
0        244296    1400705  9785367009781  Фрай М.     NaN        2009      0   
0        245728    1665067  9785942783372  Фрай М.     NaN        2010      0   
0        246246    1801350     5942783535  Фрай М.     NaN        2003      0   
0        246247    1801351  9785367016239  Фрай М.     NaN        2009      0   
0        246533    1804075  9785942783600  Фрай М.     12+        2013      1   
0        246749    1806167  9785942783877  Фрай М.     12+        2013      0   
0        246913    1807965  9785367003390  Фрай М.     NaN        2003      0   
0        246914    1807966  9785942783884  Фрай М.     12+        2009      0   
0        247198    1810879  9785367004069  Фрай М.     NaN        2003      0   
0        247199    1810880  9785942782429  Фрай М.     NaN        2006      0   
0        247200    1810881  9785367003406  Фрай М.     NaN        2009      0   
0        247406    1813266  

In [133]:
data.index = range(153)

In [135]:
df1 = pd.DataFrame()
df1 = data

In [137]:
e_hanter = urllib.parse.quote("Хантер Э.", encoding="cp1251")
url = ('https://www.chitai-gorod.ru/search/result.php?q={0}&type=author').format(e_hanter)

In [139]:
df2 = pd.DataFrame()
df2 = get_all_books(url)

1  2  3  4  5  6  7  8  9  10  11  12  13  14  15  16  17  18  19  20  21  22  23  24  25  26  27  28  29  30  31  32  33  34  35  36  37  38  39  40  41  42  43  44  45  46  47  48  49  50  51  52  53  54  55  56  57  58  59  60  61  62  63  64  65  66  67  68  69  70  71  72  73  74  75  76  77  78  79  80  81  82  83  84  85  86  87  88  89  90  91  92  93  94  95  96  97  

In [141]:
df2.index = range(97)

In [143]:
url

'https://www.chitai-gorod.ru/search/result.php?q=%C5%EC%E5%F6%20%C4.&type=author'

In [144]:
d_emec = urllib.parse.quote("Емец Д.", encoding="cp1251")
url = ('https://www.chitai-gorod.ru/search/result.php?q={0}&type=author').format(d_emec)

df3 = pd.DataFrame()
df3 = get_all_books(url)

1  2  3  4  5  6  7  8  9  10  11  12  13  14  15  16  17  18  19  20  21  22  23  24  25  26  27  28  29  30  31  32  33  34  35  36  37  38  39  40  41  42  43  44  45  46  47  48  49  50  51  52  53  54  55  56  57  58  59  60  61  62  63  64  65  66  67  68  69  70  71  72  73  74  75  76  77  78  79  80  81  82  83  84  85  86  87  88  89  90  91  92  93  94  95  96  97  98  99  100  101  102  103  104  105  106  107  108  109  110  111  112  113  114  115  116  117  118  119  120  121  122  123  124  125  126  127  128  129  130  131  132  133  134  135  136  137  138  139  140  141  142  143  144  145  146  147  148  149  150  151  152  153  154  155  156  157  158  159  160  161  162  163  164  165  166  167  168  169  170  171  172  173  174  175  176  177  178  179  180  181  182  183  184  185  186  187  188  189  190  191  

In [145]:
df0 = pd.DataFrame()
frame = [df1, df2, df3]
df0 = pd.concat(frame)
df0

ID карточки ID товара:           ISBN    Автор Возраст Год издания Голоса  \
0        244296    1400705  9785367009781  Фрай М.     NaN        2009      0   
1        245728    1665067  9785942783372  Фрай М.     NaN        2010      0   
2        246246    1801350     5942783535  Фрай М.     NaN        2003      0   
3        246247    1801351  9785367016239  Фрай М.     NaN        2009      0   
4        246533    1804075  9785942783600  Фрай М.     12+        2013      1   
5        246749    1806167  9785942783877  Фрай М.     12+        2013      0   
6        246913    1807965  9785367003390  Фрай М.     NaN        2003      0   
7        246914    1807966  9785942783884  Фрай М.     12+        2009      0   
8        247198    1810879  9785367004069  Фрай М.     NaN        2003      0   
9        247199    1810880  9785942782429  Фрай М.     NaN        2006      0   
10       247200    1810881  9785367003406  Фрай М.     NaN        2009      0   
11       247406    1813266  9785942784362  Фрай М.     NaN        2003      0   
12       248903    1890629  9785367011777  Фрай М.     NaN        2009      0   
13       253620    2289106  9785981245497  Фрай М.     NaN        2011      0   
14       256186    2293081  9785367020984  Фрай М.     NaN        2011      1   
15       259037    2297888  9785367021240  Фрай М.     NaN        2011      1   
16       259751    2298896  9785367020908  Фрай М.     NaN        2012      0   
17       259790    2298982  9785367021271  Фрай М.     NaN        2012      1   
18       266507    2309102  9785367021738  Фрай М.     NaN        2012      0   
19       266508    2309103  9785367021752  Фрай М.     NaN        2012      0   
20       268263    2311993  9785367022209  Фрай М.     NaN        2012      1   
21       270861    2024932  9785367008876  Фрай М.     NaN        2009      0   
22       271107    2026259  9785367013283  Фрай М.     12+        2014      1   
23       271108    2026260  9785942785901  Фрай М.     12+        2014      1   
24       272859    2036407  9785942786953  Фрай М.     NaN        2012      0   
25       274724    2044859  9785367004960  Фрай М.     NaN        2005      0   
26       274979    2045969  9785367021561  Фрай М.     NaN        2009      0   
27       280462    2067995  9785367021622  Фрай М.     NaN        2013      0   
28       291153    2105433  9785367021615  Фрай М.     NaN        2006      0   
29       292170    2120508  9785367004373  Фрай М.     NaN        2007      0   
..          ...        ...            ...      ...     ...         ...    ...   
0        887009    2507692  9785699844418  Емец Д.     16+        2016      0   
0        887823    2508486  9785699840465  Емец Д.     16+        2016      1   
0        899097    2517466  9785699845521  Емец Д.     16+        2016      1   
0        899624    2518066  9785699889174  Емец Д.     16+        2016      1   
0        899976    2518165  9785699845538  Емец Д.     16+        2016      0   
0        906674    2525237  9785699845552  Емец Д.     16+        2016      2   
0        912049    2529655  9785699845569  Емец Д.     16+        2016      1   
0        926308    2545413  9785699845583  Емец Д.     16+        2016      0   
0        930743    2549924  9785353078968  Емец Д.     12+        2016      0   
0        938933    2557880  9785699845590  Емец Д.     16+        2016      0   
0        949199    2566515  9785699899852  Емец Д.     12+        2017      4   
0        950639    2567167  9785699925131  Емец Д.      6+        2017      1   
0        950640    2567168  9785699925124  Емец Д.      6+        2017      0   
0        951618    2567798  9785699899883  Емец Д.     12+        2017      3   
0        961813    2577128  9785699899906  Емец Д.     12+        2017      1   
0        967444    2581615  9785699954827  Емец Д.     16+        2017      7   
0        968804    2582361  9785699928835  Емец Д.     12+        2017      1   
0        982664    2592319  9785699

In [147]:
df0.index = range(441)
df0

ID карточки ID товара:           ISBN    Автор Возраст Год издания  \
0         244296    1400705  9785367009781  Фрай М.     NaN        2009   
1         245728    1665067  9785942783372  Фрай М.     NaN        2010   
2         246246    1801350     5942783535  Фрай М.     NaN        2003   
3         246247    1801351  9785367016239  Фрай М.     NaN        2009   
4         246533    1804075  9785942783600  Фрай М.     12+        2013   
5         246749    1806167  9785942783877  Фрай М.     12+        2013   
6         246913    1807965  9785367003390  Фрай М.     NaN        2003   
7         246914    1807966  9785942783884  Фрай М.     12+        2009   
8         247198    1810879  9785367004069  Фрай М.     NaN        2003   
9         247199    1810880  9785942782429  Фрай М.     NaN        2006   
10        247200    1810881  9785367003406  Фрай М.     NaN        2009   
11        247406    1813266  9785942784362  Фрай М.     NaN        2003   
12        248903    1890629  9785367011777  Фрай М.     NaN        2009   
13        253620    2289106  9785981245497  Фрай М.     NaN        2011   
14        256186    2293081  9785367020984  Фрай М.     NaN        2011   
15        259037    2297888  9785367021240  Фрай М.     NaN        2011   
16        259751    2298896  9785367020908  Фрай М.     NaN        2012   
17        259790    2298982  9785367021271  Фрай М.     NaN        2012   
18        266507    2309102  9785367021738  Фрай М.     NaN        2012   
19        266508    2309103  9785367021752  Фрай М.     NaN        2012   
20        268263    2311993  9785367022209  Фрай М.     NaN        2012   
21        270861    2024932  9785367008876  Фрай М.     NaN        2009   
22        271107    2026259  9785367013283  Фрай М.     12+        2014   
23        271108    2026260  9785942785901  Фрай М.     12+        2014   
24        272859    2036407  9785942786953  Фрай М.     NaN        2012   
25        274724    2044859  9785367004960  Фрай М.     NaN        2005   
26        274979    2045969  9785367021561  Фрай М.     NaN        2009   
27        280462    2067995  9785367021622  Фрай М.     NaN        2013   
28        291153    2105433  9785367021615  Фрай М.     NaN        2006   
29        292170    2120508  9785367004373  Фрай М.     NaN        2007   
..           ...        ...            ...      ...     ...         ...   
411       887009    2507692  9785699844418  Емец Д.     16+        2016   
412       887823    2508486  9785699840465  Емец Д.     16+        2016   
413       899097    2517466  9785699845521  Емец Д.     16+        2016   
414       899624    2518066  9785699889174  Емец Д.     16+        2016   
415       899976    2518165  9785699845538  Емец Д.     16+        2016   
416       906674    2525237  9785699845552  Емец Д.     16+        2016   
417       912049    2529655  9785699845569  Емец Д.     16+        2016   
418       926308    2545413  9785699845583  Емец Д.     16+        2016   
419       930743    2549924  9785353078968  Емец Д.     12+        2016   
420       938933    2557880  9785699845590  Емец Д.     16+        2016   
421       949199    2566515  9785699899852  Емец Д.     12+        2017   
422       950639    2567167  9785699925131  Емец Д.      6+        2017   
423       950640    2567168  9785699925124  Емец Д.      6+        2017   
424       951618    2567798  9785699899883  Емец Д.     12+        2017   
425       961813    2577128  9785699899906  Емец Д.     12+        2017   
426       967444    2581615  9785699954827  Емец Д.     16+        2017   
427       968804    2582361  9785699928835  Емец Д.     12+        2017   
428       982664    2592319  9785699911554  Емец Д.     12+        2017   
429       993386    2600330  9785699913411  Емец Д.     12+        2017   
430       996817    2603427  9785699984985  Емец Д.     16+        2017   
431      1002042    2607833  9785699973705  Емец Д.     12+        2017   
432      1006687    2611099  9

In [148]:
df0.to_csv('hw_4.csv')